<a href="https://colab.research.google.com/github/ben-velastegui/dxc-ai-assessment/blob/main/Traces_data_wrangling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# The Zenodo data authors specify a GitHub repo with helper scripts for data exploration
# Clone the GitHub repo
!git clone https://github.com/SashoNedelkoski/multi-source-observability-dataset.git

Cloning into 'multi-source-observability-dataset'...
remote: Enumerating objects: 107, done.
remote: Counting objects: 100% (12/12), done.
remote: Compressing objects: 100% (11/11), done.
remote: Total 107 (delta 4), reused 1 (delta 1), pack-reused 95 (from 1)
Receiving objects: 100% (107/107), 1.23 MiB | 5.85 MiB/s, done.
Resolving deltas: 100% (36/36), done.


In [ ]:
# Load the zip files with the Zenodo data into Colab
!wget -O concurrent_data.zip https://zenodo.org/record/3549604/files/concurrent%20data.zip
!wget -O sequential_data.zip https://zenodo.org/record/3549604/files/sequential_data.zip


--2025-09-12 13:16:51--  https://zenodo.org/record/3549604/files/concurrent%20data.zip
Resolving zenodo.org (zenodo.org)... 188.185.43.25, 188.185.48.194, 188.185.45.92, ...
Connecting to zenodo.org (zenodo.org)|188.185.43.25|:443... connected.
HTTP request sent, awaiting response... 301 MOVED PERMANENTLY
Location: /records/3549604/files/concurrent%20data.zip [following]
--2025-09-12 13:16:52--  https://zenodo.org/records/3549604/files/concurrent%20data.zip
Reusing existing connection to zenodo.org:443.
HTTP request sent, awaiting response... 200 OK
Length: 335390038 (320M) [application/octet-stream]
Saving to: ‘concurrent_data.zip’

concurrent_data.zip 100%[===================>] 319.85M  22.0MB/s    in 2m 53s  

2025-09-12 13:19:45 (1.85 MB/s) - ‘concurrent_data.zip’ saved [335390038/335390038]

--2025-09-12 13:19:45--  https://zenodo.org/record/3549604/files/sequential_data.zip
Resolving zenodo.org (zenodo.org)... 188.185.48.194, 188.185.45.92, 188.185.43.25, ...
Connecting to zenodo

In [ ]:
# Unzip the data
!unzip -q concurrent_data.zip -d /content/
!unzip -q sequential_data.zip -d /content/


In [ ]:
# Create a measure to visualise a tree map for the file structure
import os

def print_tree(root_dir, exclude_dirs=None, indent=""):
    if exclude_dirs is None:
        exclude_dirs = []

    # List items
    items = sorted(os.listdir(root_dir))
    for i, item in enumerate(items):
        path = os.path.join(root_dir, item)
        connector = "└── " if i == len(items) - 1 else "├── "

        if os.path.isdir(path):
            if item in exclude_dirs:
                # Count files instead of listing them
                num_files = sum([len(files) for _, _, files in os.walk(path)])
                print(f"{indent}{connector}{item}/ ({num_files} files)")
            else:
                print(f"{indent}{connector}{item}/")
                # Recurse
                print_tree(path, exclude_dirs, indent + ("    " if i == len(items)-1 else "│   "))
        else:
            print(f"{indent}{connector}{item}")

# Directories/files to exclude
exclude_list = [
    "traces",
    "multi-source-observability-dataset",
    "sample_data",
    "sequential_data",
    "sequential_data.zip",
    "concurrent_data.zip",
    "traces_to_csv_modern.py",
    "config"
]

# Generate tree for /content/
print("structure:\n")
print_tree("/content/", exclude_dirs=exclude_list)


structure:

├── .config/
│   ├── .last_opt_in_prompt.yaml
│   ├── .last_survey_prompt.yaml
│   ├── .last_update_check.json
│   ├── active_config
│   ├── config_sentinel
│   ├── configurations/
│   │   └── config_default
│   ├── default_configs.db
│   ├── gce
│   ├── hidden_gcloud_config_universe_descriptor_data_cache_configs.db
│   └── logs/
│       └── 2025.09.09/
│           ├── 13.45.20.812567.log
│           ├── 13.45.50.449567.log
│           ├── 13.46.02.456374.log
│           ├── 13.46.08.280393.log
│           ├── 13.46.20.727375.log
│           └── 13.46.21.527799.log
├── .ipynb_checkpoints/
├── boot_delete_api_faults/
├── boot_delete_api_faults.csv
├── concurrent_data/
│   ├── IMPORTANT_experiment_start_end_data.txt
│   ├── logs/
│   │   ├── logs_aggregated_concurrent.csv
│   │   ├── wally113_logs.tar.gz
│   │   ├── wally117_logs.tar.gz
│   │   ├── wally122_logs.tar.gz
│   │   ├── wally123_logs.tar.gz
│   │   └── wally124_logs.tar.gz
│   ├── metrics/
│   │   ├── wally113_metr

## Run the newly created traces_to_csv_modern.py on all traces folders in the sequential data

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

!python /content/traces_to_csv_modern.py -p /content/sequential_data/traces/boot_delete/ -o /content/drive/MyDrive/traces.csv --workers 8


Mounted at /content/drive
Input dir: /content/sequential_data/traces/boot_delete/
Output CSV: /content/drive/MyDrive/traces.csv
Workers: 8
Parsing files: 100% 750/750 [00:34<00:00, 21.74file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 838438 rows to /content/drive/MyDrive/traces.csv


In [ ]:
import pandas as pd

df = pd.read_csv("/content/drive/MyDrive/traces.csv")
print(df.head(10))


       Host               Name        Service   Project  \
0  wally113          wsgi-stop         public  keystone   
1  wally113         wsgi-start         public  keystone   
2  wally113          wsgi-stop         public  keystone   
3  wally113         wsgi-start         public  keystone   
4  wally113          wsgi-stop  osapi_compute      nova   
5  wally113         wsgi-start  osapi_compute      nova   
6  wally113          wsgi-stop         public  keystone   
7  wally113         wsgi-start         public  keystone   
8  wally113   compute_api-stop  osapi_compute      nova   
9  wally113  compute_api-start  osapi_compute      nova   

                    Timestamp                          Iteration_id  \
0  2019-11-20 00:38:21.886209  02fa5206-9d0d-421c-b6f5-565822f95de9   
1  2019-11-20 00:38:21.884439  02fa5206-9d0d-421c-b6f5-565822f95de9   
2  2019-11-20 00:38:22.172826  02fa5206-9d0d-421c-b6f5-565822f95de9   
3  2019-11-20 00:38:21.890467  02fa5206-9d0d-421c-b6f5-565822f95de

In [ ]:
df

Host               Name        Service   Project  \
0       wally113          wsgi-stop         public  keystone   
1       wally113         wsgi-start         public  keystone   
2       wally113          wsgi-stop         public  keystone   
3       wally113         wsgi-start         public  keystone   
4       wally113          wsgi-stop  osapi_compute      nova   
...          ...                ...            ...       ...   
838433  wally113   neutron_api-stop  osapi_compute      nova   
838434  wally113          wsgi-stop  osapi_compute      nova   
838435  wally113         wsgi-start  osapi_compute      nova   
838436  wally113   compute_api-stop  osapi_compute      nova   
838437  wally113  compute_api-start  osapi_compute      nova   

                         Timestamp                          Iteration_id  \
0       2019-11-20 00:38:21.886209  02fa5206-9d0d-421c-b6f5-565822f95de9   
1       2019-11-20 00:38:21.884439  02fa5206-9d0d-421c-b6f5-565822f95de9   
2       2019-11-20 00:38:22.172826  02fa5206-9d0d-421c-b6f5-565822f95de9   
3       2019-11-20 00:38:21.890467  02fa5206-9d0d-421c-b6f5-565822f95de9   
4       2019-11-20 00:38:22.654374  02fa5206-9d0d-421c-b6f5-565822f95de9   
...                            ...                                   ...   
838433  2019-11-19 21:50:31.991229  fffa1061-6457-41d2-a258-6c049d3d5f2a   
838434  2019-11-19 21:50:34.078476  fffa1061-6457-41d2-a258-6c049d3d5f2a   
838435  2019-11-19 21:50:34.038938  fffa1061-6457-41d2-a258-6c049d3d5f2a   
838436  2019-11-19 21:50:34.076965  fffa1061-6457-41d2-a258-6c049d3d5f2a   
838437  2019-11-19 21:50:34.044053  fffa1061-6457-41d2-a258-6c049d3d5f2a   

                                    Trace_id  \
0       85238165-7f7e-42aa-99b6-f47918fc340f   
1       85238165-7f7e-42aa-99b6-f47918fc340f   
2       a8dd20f3-e6d8-46a6-9926-9fb2eb2605b1   
3       a8dd20f3-e6d8-46a6-9926-9fb2eb2605b1   
4       cd66c0c2-892d-4b1f-beee-98f1bf8e4929   
...                                      ...   
838433  cc113354-a20a-4862-88bd-aaf3b6b096ae   
838434  6fcd98e9-e6c6-4ebd-b130-5c354ef9b269   
838435  6fcd98e9-e6c6-4ebd-b130-5c354ef9b269   
838436  22de75cd-376b-4766-a92c-6fd3da319d29   
838437  22de75cd-376b-4766-a92c-6fd3da319d29   

                                   Parent_id  \
0       02fa5206-9d0d-421c-b6f5-565822f95de9   
1       02fa5206-9d0d-421c-b6f5-565822f95de9   
2       02fa5206-9d0d-421c-b6f5-565822f95de9   
3       02fa5206-9d0d-421c-b6f5-565822f95de9   
4       02fa5206-9d0d-421c-b6f5-565822f95de9   
...                                      ...   
838433  b7f27c00-2a02-4ebf-94e0-e9db1f0ac9f4   
838434  fffa1061-6457-41d2-a258-6c049d3d5f2a   
838435  fffa1061-6457-41d2-a258-6c049d3d5f2a   
838436  6fcd98e9-e6c6-4ebd-b130-5c354ef9b269   
838437  6fcd98e9-e6c6-4ebd-b130-5c354ef9b269   

                                     Base_id  
0       02fa5206-9d0d-421c-b6f5-565822f95de9  
1       02fa5206-9d0d-421c-b6f5-565822f95de9  
2       02fa5206-9d0d-421c-b6f5-565822f95de9  
3       02fa5206-9d0d-421c-b6f5-565822f95de9  
4       02fa5206-9d0d-421c-b6f5-565822f95de9  
...                                      ...  
838433  fffa1061-6457-41d2-a258-6c049d3d5f2a  
838434  fffa1061-6457-41d2-a258-6c049d3d5f2a  
838435  fffa1061-6457-41d2-a258-6c049d3d5f2a  
838436  fffa1061-6457-41d2-a258-6c049d3d5f2a  
838437  fffa1061-6457-41d2-a258-6c049d3d5f2a  

[838438 rows x 9 columns]

In [ ]:
!python /content/traces_to_csv_modern.py -p /content/sequential_data/traces/boot_delete/ -o /content/traces.csv --workers 8


Input dir: /content/sequential_data/traces/boot_delete/
Output CSV: /content/traces.csv
Workers: 8
Parsing files: 100% 750/750 [00:29<00:00, 25.80file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 838438 rows to /content/traces.csv


In [ ]:
!python /content/traces_to_csv_modern.py -p /content/sequential_data/traces/image_create_delete/ -o /content/image_create_delete_traces.csv --workers 8


Input dir: /content/sequential_data/traces/image_create_delete/
Output CSV: /content/image_create_delete_traces.csv
Workers: 8
Parsing files: 100% 1000/1000 [00:02<00:00, 422.30file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 22867 rows to /content/image_create_delete_traces.csv


In [ ]:
!python /content/traces_to_csv_modern.py -p /content/sequential_data/traces/network_create_delete/ -o /content/network_create_delete_traces.csv --workers 8


Input dir: /content/sequential_data/traces/network_create_delete/
Output CSV: /content/network_create_delete_traces.csv
Workers: 8
Parsing files: 100% 1000/1000 [00:06<00:00, 143.65file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 11091 rows to /content/network_create_delete_traces.csv


## Run the newly created traces_to_csv_modern.py on all traces folders in the concurrent data

In [ ]:
!python /content/traces_to_csv_modern.py -p /content/concurrent\ data/traces/boot_delete/ -o /content/concurrent_traces.csv --workers 8


Input dir: /content/concurrent data/traces/boot_delete/
Output CSV: /content/concurrent_traces.csv
Workers: 8
Parsing files: 100% 2000/2000 [00:34<00:00, 58.19file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 759858 rows to /content/concurrent_traces.csv


In [ ]:
!python /content/traces_to_csv_modern.py -p /content/concurrent\ data/traces/image_create_delete/ -o /content/image_create_delete_concurrent_traces.csv --workers 8


Input dir: /content/concurrent data/traces/image_create_delete/
Output CSV: /content/image_create_delete_concurrent_traces.csv
Workers: 8
Parsing files: 100% 3000/3000 [00:09<00:00, 316.81file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 62898 rows to /content/image_create_delete_concurrent_traces.csv


In [ ]:
!python /content/traces_to_csv_modern.py -p /content/concurrent\ data/traces/network_create_delete/ -o /content/network_create_delete_concurrent_traces.csv --workers 8


Input dir: /content/concurrent data/traces/network_create_delete/
Output CSV: /content/network_create_delete_concurrent_traces.csv
Workers: 8
Parsing files: 100% 6000/6000 [00:29<00:00, 202.84file/s]
/content/traces_to_csv_modern.py:195: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  df["Timestamp"] = pd.to_datetime(df["Timestamp"], errors="ignore")
Saved 66623 rows to /content/network_create_delete_concurrent_traces.csv


### Try to use the investigateTraces

In [ ]:
# reading.py
import pandas as pd
import os

def readTraces(operation):
    """
    Reads a trace CSV from a specific path.
    :param operation: name of the operation (without .csv)
    :return: pandas DataFrame
    """
    # full path to the CSV
    file_path = os.path.join("/content", f"{operation}.csv")
    if os.path.exists(file_path):
        df = pd.read_csv(file_path)
        return df
    else:
        raise FileNotFoundError(f"No CSV found for operation '{operation}' at {file_path}")


In [ ]:
first = readTraces('traces')


In [ ]:
first

Host               Name        Service   Project  \
0       wally113          wsgi-stop         public  keystone   
1       wally113         wsgi-start         public  keystone   
2       wally113          wsgi-stop         public  keystone   
3       wally113         wsgi-start         public  keystone   
4       wally113          wsgi-stop  osapi_compute      nova   
...          ...                ...            ...       ...   
838433  wally113   neutron_api-stop  osapi_compute      nova   
838434  wally113          wsgi-stop  osapi_compute      nova   
838435  wally113         wsgi-start  osapi_compute      nova   
838436  wally113   compute_api-stop  osapi_compute      nova   
838437  wally113  compute_api-start  osapi_compute      nova   

                         Timestamp                          Iteration_id  \
0       2019-11-20 00:04:53.900608  006e8555-8c25-4462-9927-0033be8472e3   
1       2019-11-20 00:04:53.898661  006e8555-8c25-4462-9927-0033be8472e3   
2       2019-11-20 00:04:54.184492  006e8555-8c25-4462-9927-0033be8472e3   
3       2019-11-20 00:04:53.904399  006e8555-8c25-4462-9927-0033be8472e3   
4       2019-11-20 00:04:54.732996  006e8555-8c25-4462-9927-0033be8472e3   
...                            ...                                   ...   
838433  2019-11-19 22:44:52.544489  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   
838434  2019-11-19 22:44:54.603424  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   
838435  2019-11-19 22:44:54.561400  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   
838436  2019-11-19 22:44:54.602107  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   
838437  2019-11-19 22:44:54.567091  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   

                                    Trace_id  \
0       5172cbe3-6af4-4013-b794-31f00a8624b5   
1       5172cbe3-6af4-4013-b794-31f00a8624b5   
2       d689524b-9d5c-4961-89f1-ca003569f33f   
3       d689524b-9d5c-4961-89f1-ca003569f33f   
4       d04340e8-e895-4399-b3da-6e2383bd07e5   
...                                      ...   
838433  7a7be7d1-d01a-48a0-b3f1-755477e86229   
838434  dc8759da-a7fa-4040-b656-2f2f3f40ddcd   
838435  dc8759da-a7fa-4040-b656-2f2f3f40ddcd   
838436  cd4d28d1-b27f-4fa7-95c3-0d77d10fa193   
838437  cd4d28d1-b27f-4fa7-95c3-0d77d10fa193   

                                   Parent_id  \
0       006e8555-8c25-4462-9927-0033be8472e3   
1       006e8555-8c25-4462-9927-0033be8472e3   
2       006e8555-8c25-4462-9927-0033be8472e3   
3       006e8555-8c25-4462-9927-0033be8472e3   
4       006e8555-8c25-4462-9927-0033be8472e3   
...                                      ...   
838433  b67a8913-20d8-46c2-95a0-0c5185b7520a   
838434  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   
838435  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221   
838436  dc8759da-a7fa-4040-b656-2f2f3f40ddcd   
838437  dc8759da-a7fa-4040-b656-2f2f3f40ddcd   

                                     Base_id  
0       006e8555-8c25-4462-9927-0033be8472e3  
1       006e8555-8c25-4462-9927-0033be8472e3  
2       006e8555-8c25-4462-9927-0033be8472e3  
3       006e8555-8c25-4462-9927-0033be8472e3  
4       006e8555-8c25-4462-9927-0033be8472e3  
...                                      ...  
838433  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221  
838434  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221  
838435  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221  
838436  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221  
838437  ff684ff4-f5cf-4bc3-a1f1-e12d87c18221  

[838438 rows x 9 columns]

In [ ]:
import os
import shutil

# source folder containing your CSVs
source_folder = "/content"

# target folder to store CSVs
target_folder = os.path.join(source_folder, "traces_csv")

# create target folder if it doesn't exist
os.makedirs(target_folder, exist_ok=True)

# loop through files in source folder (not subdirectories)
for file_name in os.listdir(source_folder):
    if file_name.endswith(".csv"):
        src_path = os.path.join(source_folder, file_name)
        dst_path = os.path.join(target_folder, file_name)
        shutil.copy2(src_path, dst_path)  # copy with metadata

print(f"Copied {len(os.listdir(target_folder))} CSV files to {target_folder}")


Copied 6 CSV files to /content/traces_csv


In [ ]:
import os
import shutil

source_folder = "/content"
target_folder = os.path.join(source_folder, "traces_csv")
os.makedirs(target_folder, exist_ok=True)

# remove duplicates in source that already exist in target
for file_name in os.listdir(source_folder):
    if file_name.endswith(".csv"):
        src_path = os.path.join(source_folder, file_name)
        dst_path = os.path.join(target_folder, file_name)
        if os.path.exists(dst_path):
            os.remove(src_path)  # delete duplicate in source

# move remaining CSVs
moved_count = 0
for file_name in os.listdir(source_folder):
    if file_name.endswith(".csv"):
        src_path = os.path.join(source_folder, file_name)
        dst_path = os.path.join(target_folder, file_name)
        shutil.move(src_path, dst_path)
        moved_count += 1

print(f"Moved {moved_count} CSV files to {target_folder}")


Moved 0 CSV files to /content/traces_csv


In [ ]:
import os
import shutil

# Base folder where your CSVs are currently
base_csv_folder = "/content/traces_csv"

# Mapping of target folders to source files
file_map = {
    "boot_delete_api_faults": ["traces.csv", "concurrent_traces.csv"],
    "create_delete_image": ["image_create_delete_traces.csv", "image_create_delete_concurrent_traces.csv"],
    "network_create_delete": ["network_create_delete_traces.csv", "network_create_delete_concurrent_traces.csv"]
}

# Create folders and move files
for folder, files in file_map.items():
    target_folder = os.path.join(base_csv_folder, folder)
    os.makedirs(target_folder, exist_ok=True)
    for file in files:
        src = os.path.join(base_csv_folder, file)
        dst = os.path.join(target_folder, file)
        if os.path.exists(src):
            shutil.move(src, dst)
        else:
            print(f"Warning: {src} not found.")


In [ ]:
# Create a measure to visualise a tree map for the file structure
import os

def print_tree(root_dir, exclude_dirs=None, indent=""):
    if exclude_dirs is None:
        exclude_dirs = []

    # List items
    items = sorted(os.listdir(root_dir))
    for i, item in enumerate(items):
        path = os.path.join(root_dir, item)
        connector = "└── " if i == len(items) - 1 else "├── "

        if os.path.isdir(path):
            if item in exclude_dirs:
                # Count files instead of listing them
                num_files = sum([len(files) for _, _, files in os.walk(path)])
                print(f"{indent}{connector}{item}/ ({num_files} files)")
            else:
                print(f"{indent}{connector}{item}/")
                # Recurse
                print_tree(path, exclude_dirs, indent + ("    " if i == len(items)-1 else "│   "))
        else:
            print(f"{indent}{connector}{item}")

# Directories/files to exclude
exclude_list = [
    "concurrent data",
    "multi-source-observability-dataset",
    "sample_data",
    "sequential_data",
    "sequential_data.zip",
    "concurrent_data.zip",
    "traces_to_csv_modern.py",
    "config"
]

# Generate tree for /content/
print("traces_csv structure:\n")
print_tree("/content/", exclude_dirs=exclude_list)


traces_csv structure:

├── .config/
│   ├── .last_opt_in_prompt.yaml
│   ├── .last_survey_prompt.yaml
│   ├── .last_update_check.json
│   ├── active_config
│   ├── config_sentinel
│   ├── configurations/
│   │   └── config_default
│   ├── default_configs.db
│   ├── gce
│   ├── hidden_gcloud_config_universe_descriptor_data_cache_configs.db
│   └── logs/
│       └── 2025.09.09/
│           ├── 13.45.20.812567.log
│           ├── 13.45.50.449567.log
│           ├── 13.46.02.456374.log
│           ├── 13.46.08.280393.log
│           ├── 13.46.20.727375.log
│           └── 13.46.21.527799.log
├── boot_delete_api_faults/
│   ├── concurrent_traces.csv
│   └── traces.csv
├── concurrent data/ (11018 files)
├── concurrent_data.zip
├── create_delete_image/
│   ├── image_create_delete_concurrent_traces.csv
│   └── image_create_delete_traces.csv
├── multi-source-observability-dataset/ (63 files)
├── network_create_delete/
│   ├── network_create_delete_concurrent_traces.csv
│   └── network_create_de

In [ ]:
# Move all CSV files to /content/
!mv /content/boot_delete_api_faults/*.csv /content/
!mv /content/create_delete_image/*.csv /content/
!mv /content/network_create_delete/*.csv /content/


In [ ]:
import sys
sys.path.append("/content/multi-source-observability-dataset")


In [ ]:
%%bash
REPO="/content/multi-source-observability-dataset"
SCRIPT="$REPO/workloads/json_trace_ids.py"
OUT="/content/sequential_trace_ids_all.txt"

rm -f "$OUT"
for f in /content/sequential_data/traces/*/*.json; do
    python "$SCRIPT" "$f" | sed "s|^|$f,|" >> "$OUT"
done

echo "✅ Done. Trace IDs saved to $OUT"
wc -l "$OUT"


✅ Done. Trace IDs saved to /content/sequential_trace_ids_all.txt
2750 /content/sequential_trace_ids_all.txt


Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    for i in range(len(trace_json['tasks'][0]['subtasks'][0]['workloads'][0]['data'])):
                       ~~~~~~~~~~^^^^^^^^^
KeyError: 'tasks'
Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    for i in range(len(trace_json['tasks'][0]['subtasks'][0]['workloads'][0]['data'])):
                       ~~~~~~~~~~^^^^^^^^^
KeyError: 'tasks'
Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    for i in range(len(trace_json['tasks'][0]['subtasks'][0]['workloads'][0]['data'])):
                       ~~~~~~~~~~^^^^^^^^^
KeyError: 'tasks'
Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    f

In [ ]:
%%bash
REPO="/content/multi-source-observability-dataset"
SCRIPT="$REPO/workloads/json_trace_ids.py"
OUT="/content/concurrent_data/trace_ids_all.txt"

rm -f "$OUT"
for f in /content/concurrent_data/traces/*/*.json; do
    python "$SCRIPT" "$f" | sed "s|^|$f,|" >> "$OUT"
done

echo "✅ Done. Trace IDs saved to $OUT"
wc -l "$OUT"


✅ Done. Trace IDs saved to /content/concurrent_data/trace_ids_all.txt
11000 /content/concurrent_data/trace_ids_all.txt


Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    for i in range(len(trace_json['tasks'][0]['subtasks'][0]['workloads'][0]['data'])):
                       ~~~~~~~~~~^^^^^^^^^
KeyError: 'tasks'
Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    for i in range(len(trace_json['tasks'][0]['subtasks'][0]['workloads'][0]['data'])):
                       ~~~~~~~~~~^^^^^^^^^
KeyError: 'tasks'
Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    for i in range(len(trace_json['tasks'][0]['subtasks'][0]['workloads'][0]['data'])):
                       ~~~~~~~~~~^^^^^^^^^
KeyError: 'tasks'
Traceback (most recent call last):
  File "/content/multi-source-observability-dataset/workloads/json_trace_ids.py", line 9, in <module>
    f

In [ ]:
import json

def extract_trace_ids(node):
    ids = []
    # If the node itself has a trace_id, grab it
    if isinstance(node, dict) and 'trace_id' in node:
        ids.append(node['trace_id'])
    # Recurse into any children
    if isinstance(node, dict):
        for child in node.get('children', []):
            ids.extend(extract_trace_ids(child))
    elif isinstance(node, list):
        for item in node:
            ids.extend(extract_trace_ids(item))
    return ids

file_path = "/content/sequential_data/traces/boot_delete/0030f2fb-a30d-4a9a-92e1-f1e383355afc.json"
with open(file_path) as f:
    data = json.load(f)

trace_ids = extract_trace_ids(data)
print(trace_ids)


['a0bcc281-6c3b-420c-a513-e004a6f50488', '1f7a1654-6dc5-4323-a98a-0f3640f183f2', 'c487705a-a3ee-463f-b05d-444e272db0f6', 'f4628a15-e491-4d0c-b0f0-fe7c45853b33', 'b2917e0a-1bec-4732-8672-504ef0bf753c', '086d11b4-2881-4dcb-8367-2b600f913eeb', '3a110acb-493c-447e-a4aa-39a507153846', 'ff3820bd-e7c3-4bca-8b83-a8bd40e4b97a', '76ce5f7a-988a-493e-8458-cdbdcff8871b', 'cc7d4c10-1f94-4a35-baa4-d9bc67c5d7d6', 'dcc618ea-7814-4965-9ad9-5e27819679b0', '675c63e5-ac95-4750-a8b1-47efd2c7af95', '5c93f735-5ac1-46ca-81b4-37be95a12f28', '466ddd2e-baef-478a-ab46-01921279e1b2', 'd0d2f57e-3d4d-471e-96b6-4ae89b91973f', '27223762-be96-446b-9971-041ba42f4ace', '9c241750-2599-48d0-b312-68bef66c11bd', 'df7d287c-36b9-4279-908b-3efe8841e4f1', 'd2525b3e-eac4-4e44-8560-8f9f5b8e21b9', '1d62796d-d387-4ebb-862a-3b480e8a57fc', '606bc424-98a1-40ef-a731-bd3b56d1a855', 'c5665d0d-f83b-4823-b14c-552076607abc', '0cb9d8c3-eda9-4666-a815-80d855bbd333', '1979f566-d4c3-422a-bf38-41fcd1ba8ed7', '2e607b3d-6c10-4fce-9609-c570c5e4c8e7',

In [ ]:
import json
import os

def extract_trace_ids(node):
    """Recursively extract all trace_id values from a JSON node."""
    ids = []
    if isinstance(node, dict):
        if 'trace_id' in node:
            ids.append(node['trace_id'])
        for value in node.values():
            ids.extend(extract_trace_ids(value))
    elif isinstance(node, list):
        for item in node:
            ids.extend(extract_trace_ids(item))
    return ids

# Directories containing the JSON trace files
trace_dirs = [
    "sequential_data/traces",
    "concurrent_data/traces"
]

# Iterate through all JSON files in the trace directories
for trace_dir in trace_dirs:
    for root, _, files in os.walk(trace_dir):
        for file_name in files:
            if file_name.endswith(".json"):
                file_path = os.path.join(root, file_name)
                try:
                    with open(file_path) as f:
                        data = json.load(f)
                    trace_ids = extract_trace_ids(data)
                    for tid in trace_ids:
                        print(f"{file_path}: {tid}")
                except Exception as e:
                    print(f"Error reading {file_path}: {e}")


Streaming output truncated to the last 5000 lines.
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 4b2c314b-149e-41fc-a3ed-2aa324b5d49f
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 4b2c314b-149e-41fc-a3ed-2aa324b5d49f
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 3b3a8b08-28f6-41dd-8c63-b607c75ac66c
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 3b3a8b08-28f6-41dd-8c63-b607c75ac66c
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 3b3a8b08-28f6-41dd-8c63-b607c75ac66c
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 3aa8ec69-07a0-4007-bc0e-ff0993e905bc
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-3709458b57c5.json: 3aa8ec69-07a0-4007-bc0e-ff0993e905bc
concurrent_data/traces/network_create_delete/848792f9-74e1-4026-9094-37094

In [ ]:
import json
import os
import csv

def extract_trace_ids(node):
    """Recursively extract all trace_id values from a JSON node."""
    ids = []
    if isinstance(node, dict):
        if 'trace_id' in node:
            ids.append(node['trace_id'])
        for value in node.values():
            ids.extend(extract_trace_ids(value))
    elif isinstance(node, list):
        for item in node:
            ids.extend(extract_trace_ids(item))
    return ids

trace_dirs = [
    "sequential_data/traces",
    "concurrent_data/traces"
]

output_file = "all_trace_ids.csv"

with open(output_file, mode='w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['file_path', 'trace_id'])  # header

    for trace_dir in trace_dirs:
        for root, _, files in os.walk(trace_dir):
            for file_name in files:
                if file_name.endswith(".json"):
                    file_path = os.path.join(root, file_name)
                    try:
                        with open(file_path) as f:
                            data = json.load(f)
                        trace_ids = extract_trace_ids(data)
                        for tid in trace_ids:
                            writer.writerow([file_path, tid])
                    except Exception as e:
                        print(f"Error reading {file_path}: {e}")

print(f"All trace IDs saved to {output_file}")


All trace IDs saved to all_trace_ids.csv


In [ ]:
import json
import os
import csv

def extract_trace_ids(node):
    """Recursively extract all trace_id values from a JSON node."""
    ids = []
    if isinstance(node, dict):
        if 'trace_id' in node:
            ids.append(node['trace_id'])
        for value in node.values():
            ids.extend(extract_trace_ids(value))
    elif isinstance(node, list):
        for item in node:
            ids.extend(extract_trace_ids(item))
    return ids

# Directories containing the JSON trace files
trace_dirs = {
    "/content/sequential_data/traces": "sequential_trace_ids.csv",
    "/content/concurrent data/traces": "concurrent_trace_ids.csv"
}

# Process each directory and write results to a CSV file
for trace_dir, csv_file in trace_dirs.items():
    rows = []

    for root, _, files in os.walk(trace_dir):
        for file_name in files:
            if file_name.endswith(".json"):
                file_path = os.path.join(root, file_name)
                try:
                    with open(file_path) as f:
                        data = json.load(f)
                    trace_ids = extract_trace_ids(data)
                    for tid in trace_ids:
                        rows.append([file_path, tid])
                except Exception as e:
                    print(f"Error reading {file_path}: {e}")

    # Write results to CSV
    if rows:
        with open(csv_file, mode="w", newline="") as f:
            writer = csv.writer(f)
            writer.writerow(["file_path", "trace_id"])
            writer.writerows(rows)

        print(f"Saved {len(rows)} trace IDs to {csv_file}")
    else:
        print(f"No trace IDs found in {trace_dir}")


Saved 2488675 trace IDs to sequential_trace_ids.csv
Saved 5070334 trace IDs to concurrent_trace_ids.csv


In [ ]:
import json
import os
import csv

def extract_trace_ids(node):
    """Recursively extract all trace_id values from a JSON node."""
    ids = []
    if isinstance(node, dict):
        if 'trace_id' in node:
            ids.append(node['trace_id'])
        for value in node.values():
            ids.extend(extract_trace_ids(value))
    elif isinstance(node, list):
        for item in node:
            ids.extend(extract_trace_ids(item))
    return ids

# Directories and output CSV files
trace_dirs = {

    "/content/concurrent data/traces": "concurrent_trace_ids.csv"
}

CHUNK_SIZE = 2_535_167  # rows per chunk

for trace_dir, csv_file in trace_dirs.items():
    rows = []
    chunk_index = 1
    total_rows = 0

    for root, _, files in os.walk(trace_dir):
        for file_name in files:
            if file_name.endswith(".json"):
                file_path = os.path.join(root, file_name)
                try:
                    with open(file_path) as f:
                        data = json.load(f)
                    trace_ids = extract_trace_ids(data)
                    for tid in trace_ids:
                        rows.append([file_path, tid])

                        # If chunk size reached → save to disk
                        if len(rows) >= CHUNK_SIZE:
                            chunk_file = csv_file.replace(".csv", f"_part{chunk_index}.csv")
                            with open(chunk_file, mode="w", newline="") as f:
                                writer = csv.writer(f)
                                writer.writerow(["file_path", "trace_id"])
                                writer.writerows(rows)
                            print(f"Saved {len(rows)} rows to {chunk_file}")
                            total_rows += len(rows)
                            rows = []  # reset buffer
                            chunk_index += 1
                except Exception as e:
                    print(f"Error reading {file_path}: {e}")

    # Write leftover rows
    if rows:
        chunk_file = csv_file.replace(".csv", f"_part{chunk_index}.csv")
        with open(chunk_file, mode="w", newline="") as f:
            writer = csv.writer(f)
            writer.writerow(["file_path", "trace_id"])
            writer.writerows(rows)
        print(f"Saved {len(rows)} rows to {chunk_file}")
        total_rows += len(rows)

    print(f"✅ Finished {trace_dir}: total {total_rows} trace IDs written in {chunk_index} part(s).")


Saved 2535167 rows to concurrent_trace_ids_part1.csv
Saved 2535167 rows to concurrent_trace_ids_part2.csv
✅ Finished /content/concurrent data/traces: total 5070334 trace IDs written in 3 part(s).
